<H1>Question 1 </H1>

<H4>Import Toronto list of Postal Codes </H>

In [50]:
import pandas as pd
url='https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
df=pd.read_html(url, header=0)[0]
df.head(5)

Postcode           Borough      Neighborhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront

<H4>Only the cells that have an assigned borough. Ignore cells with a borough that is Not assigned

In [51]:
# Get names of indexes for which column Borough has value "Not assigned"
indexNames = df[ df['Borough'] =='Not assigned'].index

# Delete these row indexes from dataFrame
df.drop(indexNames , inplace=True)

df.head(10)

Postcode           Borough      Neighborhood
2       M3A        North York         Parkwoods
3       M4A        North York  Victoria Village
4       M5A  Downtown Toronto      Harbourfront
5       M6A        North York  Lawrence Heights
6       M6A        North York    Lawrence Manor
7       M7A      Queen's Park      Not assigned
9       M9A  Downtown Toronto      Queen's Park
10      M1B       Scarborough             Rouge
11      M1B       Scarborough           Malvern
13      M3B        North York   Don Mills North

<H4>If a cell has a borough but a Not assigned neighborhood, then the neighborhood will be the same as the borough

In [52]:
df.loc[df['Neighborhood'] =='Not assigned' , 'Neighborhood'] = df['Borough']
df.head(10)

Postcode           Borough      Neighborhood
2       M3A        North York         Parkwoods
3       M4A        North York  Victoria Village
4       M5A  Downtown Toronto      Harbourfront
5       M6A        North York  Lawrence Heights
6       M6A        North York    Lawrence Manor
7       M7A      Queen's Park      Queen's Park
9       M9A  Downtown Toronto      Queen's Park
10      M1B       Scarborough             Rouge
11      M1B       Scarborough           Malvern
13      M3B        North York   Don Mills North

In [53]:
result = df.groupby(['Postcode','Borough'], sort=False).agg( ', '.join)

In [54]:
df_new=result.reset_index()
df_new.head(10)

Postcode           Borough                      Neighborhood
0      M3A        North York                         Parkwoods
1      M4A        North York                  Victoria Village
2      M5A  Downtown Toronto                      Harbourfront
3      M6A        North York  Lawrence Heights, Lawrence Manor
4      M7A      Queen's Park                      Queen's Park
5      M9A  Downtown Toronto                      Queen's Park
6      M1B       Scarborough                    Rouge, Malvern
7      M3B        North York                   Don Mills North
8      M4B         East York   Woodbine Gardens, Parkview Hill
9      M5B  Downtown Toronto          Ryerson, Garden District

<H4> Save a copy in csv format

In [55]:
df.to_csv('Neighborhoods_in_Toronto_Data.csv',index=False)

<H4>use the .shape method to print the number of rows of your dataframe

In [56]:
df_new.shape

(103, 3)

<H1>Question 2 </H1>

<H4>Using geographical coordinates of each postal code: http://cocl.us/Geospatial_data</H>

In [57]:
import numpy as np
import pandas as pd
!pip install geocoder

print('Libraries imported.')

Libraries imported.


<H4>Reading  Neighborhoods_in_Toronto_Data.csv that was previously saved

In [58]:
df = pd.read_csv('Neighborhoods_in_Toronto_Data.csv')
df.head()

Postcode           Borough      Neighborhood
0      M3A        North York         Parkwoods
1      M4A        North York  Victoria Village
2      M5A  Downtown Toronto      Harbourfront
3      M6A        North York  Lawrence Heights
4      M6A        North York    Lawrence Manor

<H4> Downloading copy of Geospatial_data

In [59]:
!wget -q -O 'Toronto_long_lat_data.csv'  http://cocl.us/Geospatial_data
df_lon_lat = pd.read_csv('Toronto_long_lat_data.csv')
df_lon_lat.columns=['Postalcode','Latitude','Longitude']
df_lon_lat.head()

Postalcode   Latitude  Longitude
0        M1B  43.806686 -79.194353
1        M1C  43.784535 -79.160497
2        M1E  43.763573 -79.188711
3        M1G  43.770992 -79.216917
4        M1H  43.773136 -79.239476

<H4>Saving copy of Geospatial_data in csv format

In [60]:
df_lon_lat.to_csv('Geospatial_Coordinates.csv',index=False)

<H4> Reading Geospatial_Coordinates.csv into dataframe

In [61]:
# transform the csv file with the coordinates into a dataframe
coordinates_df = pd.read_csv('Geospatial_Coordinates.csv') 
coordinates_df.shape
coordinates_df.head()

Postalcode   Latitude  Longitude
0        M1B  43.806686 -79.194353
1        M1C  43.784535 -79.160497
2        M1E  43.763573 -79.188711
3        M1G  43.770992 -79.216917
4        M1H  43.773136 -79.239476

<H4>Joining Geospatial data and Toronto on Postalcode/PostCode<H/>

In [62]:
postcodes_with_coordinates_df = df.join(coordinates_df.set_index('Postalcode'), on='Postcode')

postcodes_with_coordinates_df.head(12)

Postcode           Borough      Neighborhood   Latitude  Longitude
0       M3A        North York         Parkwoods  43.753259 -79.329656
1       M4A        North York  Victoria Village  43.725882 -79.315572
2       M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636
3       M6A        North York  Lawrence Heights  43.718518 -79.464763
4       M6A        North York    Lawrence Manor  43.718518 -79.464763
5       M7A      Queen's Park      Queen's Park  43.662301 -79.389494
6       M9A  Downtown Toronto      Queen's Park  43.667856 -79.532242
7       M1B       Scarborough             Rouge  43.806686 -79.194353
8       M1B       Scarborough           Malvern  43.806686 -79.194353
9       M3B        North York   Don Mills North  43.745906 -79.352188
10      M4B         East York  Woodbine Gardens  43.706397 -79.309937
11      M4B         East York     Parkview Hill  43.706397 -79.309937

<H4>Save a copy of the joined dataframe in csv

In [63]:
postcodes_with_coordinates_df.to_csv('Neighborhoods_in_Toronto_Coordinates.csv',index=False)

<H1>Question 3</H1>

<H2>Explore and cluster the neighborhoods in Toronto

<H4>Use geopy library to get the latitude and longitude values of New York City

In [68]:
df = pd.read_csv('Neighborhoods_in_Toronto_Coordinates.csv')
df.head()

Postcode           Borough      Neighborhood   Latitude  Longitude
0      M3A        North York         Parkwoods  43.753259 -79.329656
1      M4A        North York  Victoria Village  43.725882 -79.315572
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636
3      M6A        North York  Lawrence Heights  43.718518 -79.464763
4      M6A        North York    Lawrence Manor  43.718518 -79.464763

In [65]:

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [66]:
address = 'Toronto, ON'

geolocator = Nominatim(user_agent="Toronto")
location = geolocator.geocode(address)
latitude_toronto = location.latitude
longitude_toronto = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude_toronto, longitude_toronto))

The geograpical coordinate of Toronto are 43.653963, -79.387207.


<H4>Displaying map of Toronto

In [69]:

map_toronto = folium.Map(location=[latitude_toronto, longitude_toronto], zoom_start=10)

# add markers to map
for lat, lng, borough, Neighbourhood in zip(df['Latitude'], df['Longitude'], df['Borough'], df['Neighborhood']):
    label = '{}, {}'.format(Neighbourhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

<H4>Define Foursquare Credentials and Version

In [71]:

CLIENT_ID = 'WJR5DQDPRMUNTMUWUHZSJE2M3WEDNAV3DUDIOKFDXDNTZH3C' # your Foursquare ID
CLIENT_SECRET = 'ZGDT1DQ1BPP22BEVG00WR0XJ2IK0HK1G5JZLJXFGSLLVKSUQ' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: WJR5DQDPRMUNTMUWUHZSJE2M3WEDNAV3DUDIOKFDXDNTZH3C
CLIENT_SECRET:ZGDT1DQ1BPP22BEVG00WR0XJ2IK0HK1G5JZLJXFGSLLVKSUQ


In [72]:
# defining radius and limit of venues to get
radius=500
LIMIT=100

In [73]:

def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [76]:
toronto_venues = getNearbyVenues(names=df['Neighborhood'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )

Parkwoods
Victoria Village
Harbourfront
Lawrence Heights
Lawrence Manor
Queen's Park
Queen's Park
Rouge
Malvern
Don Mills North
Woodbine Gardens
Parkview Hill
Ryerson
Garden District
Glencairn
Cloverdale
Islington
Martin Grove
Princess Gardens
West Deane Park
Highland Creek
Rouge Hill
Port Union
Flemingdon Park
Don Mills South
Woodbine Heights
St. James Town
Humewood-Cedarvale
Bloordale Gardens
Eringate
Markland Wood
Old Burnhamthorpe
Guildwood
Morningside
West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor
Downsview North
Wilson Heights
Thorncliffe Park
Adelaide
King
Richmond
Dovercourt Village
Dufferin
Scarborough Village
Fairview
Henry Farm
Oriole
Northwood Park
York University
East Toronto
Harbourfront East
Toronto Islands
Union Station
Little Portugal
Trinity
East Birchmount Park
Ionview
Kennedy Park
Bayview Village
CFB Toronto
Downsview East
The Danforth West
Riverdale
Design Exchange
Toronto 

<H4> Displaying Toronto_Venues dataframe

In [77]:
toronto_venues.head(10)

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0         Parkwoods               43.753259               -79.329656   
1         Parkwoods               43.753259               -79.329656   
2         Parkwoods               43.753259               -79.329656   
3  Victoria Village               43.725882               -79.315572   
4  Victoria Village               43.725882               -79.315572   
5  Victoria Village               43.725882               -79.315572   
6  Victoria Village               43.725882               -79.315572   
7      Harbourfront               43.654260               -79.360636   
8      Harbourfront               43.654260               -79.360636   
9      Harbourfront               43.654260               -79.360636   

                         Venue  Venue Latitude  Venue Longitude  \
0              Brookbanks Park       43.751976       -79.332140   
1  Careful & Reliable Painting       43.752622       -79.331957   
2                Variety Store       43.751974       -79.333114   
3       Victoria Village Arena       43.723481       -79.315635   
4                  Tim Hortons       43.725517       -79.313103   
5                    Portugril       43.725819       -79.312785   
6                   Pizza Nova       43.725824       -79.312860   
7             Roselle Desserts       43.653447       -79.362017   
8                Tandem Coffee       43.653559       -79.361809   
9       Cooper Koo Family YMCA       43.653191       -79.357947   

               Venue Category  
0                        Park  
1  Construction & Landscaping  
2           Food & Drink Shop  
3                Hockey Arena  
4                 Coffee Shop  
5       Portuguese Restaurant  
6                 Pizza Place  
7                      Bakery  
8                 Coffee Shop  
9        Gym / Fitness Center

In [78]:
toronto_venues.shape

(4296, 7)

In [79]:
toronto_venues.groupby('Neighbourhood').count()

Neighbourhood Latitude  \
Neighbourhood                                                               
Adelaide                                                              100   
Agincourt                                                               5   
Agincourt North                                                         2   
Albion Gardens                                                          8   
Alderwood                                                              10   
Bathurst Manor                                                         20   
Bathurst Quay                                                          15   
Bayview Village                                                         4   
Beaumond Heights                                                        8   
Bedford Park                                                           22   
Berczy Park                                                            56   
Birch Cliff                                                             4   
Bloordale Gardens                                                       8   
Brockton                                                               24   
Business Reply Mail Processing Centre 969 Eastern                      17   
CFB Toronto                                                             2   
CN Tower                                                               15   
Cabbagetown                                                            46   
Caledonia-Fairbanks                                                     5   
Canada Post Gateway Processing Centre                                  11   
Cedarbrae                                                               9   
Central Bay Street                                                     83   
Chinatown                                                              92   
Christie                                                               17   
Church and Wellesley                                                   86   
Clairlea                                                                9   
Clarks Corners                                                         13   
Cliffcrest                                                              3   
Cliffside                                                               3   
Cliffside West                                                          4   
Cloverdale                                                              1   
Commerce Court                                                        100   
Davisville                                                             36   
Davisville North                                                        8   
Deer Park                                                              15   
Del Ray                                                                 4   
Design Exchange                                                       100   
Don Mills North                                                         5   
Don Mills South                                                        23   
Dorset Park                                                             7   
Dovercourt Village                                                     16   
Downsview                                                               4   
Downsview Central                                                       2   
Downsview East                                                          2   
Downsview North                                                        20   
Downsview Northwest                                                     5   
Downsview West                                                          5   
Dufferin                                                               16   
East Birchmount Park                                                    4   
East Toronto                                                            4   
Emery                                          

<H4>Analysing Each Neighborhood

In [81]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighbourhood'] = toronto_venues['Neighbourhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot.head(20)

Accessories Store  Afghan Restaurant  Airport  Airport Food Court  \
0                   0                  0        0                   0   
1                   0                  0        0                   0   
2                   0                  0        0                   0   
3                   0                  0        0                   0   
4                   0                  0        0                   0   
5                   0                  0        0                   0   
6                   0                  0        0                   0   
7                   0                  0        0                   0   
8                   0                  0        0                   0   
9                   0                  0        0                   0   
10                  0                  0        0                   0   
11                  0                  0        0                   0   
12                  0                  0        0                   0   
13                  0                  0        0                   0   
14                  0                  0        0                   0   
15                  0                  0        0                   0   
16                  0                  0        0                   0   
17                  0                  0        0                   0   
18                  0                  0        0                   0   
19                  0                  0        0                   0   

    Airport Gate  Airport Lounge  Airport Service  Airport Terminal  \
0              0               0                0                 0   
1              0               0                0                 0   
2              0               0                0                 0   
3              0               0                0                 0   
4              0               0                0                 0   
5              0               0                0                 0   
6              0               0                0                 0   
7              0               0                0                 0   
8              0               0                0                 0   
9              0               0                0                 0   
10             0               0                0                 0   
11             0               0                0                 0   
12             0               0                0                 0   
13             0               0                0                 0   
14             0               0                0                 0   
15             0               0                0                 0   
16             0               0                0                 0   
17             0               0                0                 0   
18             0               0                0                 0   
19             0               0                0                 0   

    American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                     0             0         0            0   
1                     0             0         0            0   
2                     0             0         0            0   
3                     0             0         0            0   
4                     0             0         0            0   
5                     0             0         0            0   
6                     0             0         0            0   
7                     0             0         0            0   
8                     0             0         0            0   
9                     0             0         0            0   
10                    0             0         0            0   
11                    0             0         0            0   
12                    0             0         0            0   
13                    0             0         0            0   
14                

In [82]:
toronto_onehot.shape

(4296, 270)

<H4>Group rows by neighborhood and taking the mean of the frequency of occurrence of each category

In [83]:
toronto_grouped = toronto_onehot.groupby('Neighbourhood').mean().reset_index()
toronto_grouped

Neighbourhood  Accessories Store  \
0                                             Adelaide           0.000000   
1                                            Agincourt           0.000000   
2                                      Agincourt North           0.000000   
3                                       Albion Gardens           0.000000   
4                                            Alderwood           0.000000   
5                                       Bathurst Manor           0.000000   
6                                        Bathurst Quay           0.000000   
7                                      Bayview Village           0.000000   
8                                     Beaumond Heights           0.000000   
9                                         Bedford Park           0.000000   
10                                         Berczy Park           0.000000   
11                                         Birch Cliff           0.000000   
12                                   Bloordale Gardens           0.000000   
13                                            Brockton           0.000000   
14   Business Reply Mail Processing Centre 969 Eastern           0.000000   
15                                         CFB Toronto           0.000000   
16                                            CN Tower           0.000000   
17                                         Cabbagetown           0.000000   
18                                 Caledonia-Fairbanks           0.000000   
19               Canada Post Gateway Processing Centre           0.000000   
20                                           Cedarbrae           0.000000   
21                                  Central Bay Street           0.000000   
22                                           Chinatown           0.000000   
23                                            Christie           0.000000   
24                                Church and Wellesley           0.000000   
25                                            Clairlea           0.000000   
26                                      Clarks Corners           0.000000   
27                                          Cliffcrest           0.000000   
28                                           Cliffside           0.000000   
29                                      Cliffside West           0.000000   
30                                          Cloverdale           0.000000   
31                                      Commerce Court           0.000000   
32                                          Davisville           0.000000   
33                                    Davisville North           0.000000   
34                                           Deer Park           0.000000   
35                                             Del Ray           0.000000   
36                                     Design Exchange           0.000000   
37                                     Don Mills North           0.000000   
38                                     Don Mills South           0.000000   
39                                         Dorset Park           0.000000   
40                                  Dovercourt Village           0.000000   
41                                           Downsview           0.000000   
42                                   Downsview Central           0.000000   
43                                      Downsview East           0.000000   
44                                     Downsview North           0.000000   
45                                 Downsview Northwest           0.000000   
46                                      Downsview West           0.000000   
47                                            Dufferin           0.000000   
48                                East Birchmount Park           0.000000   
49                                        East Toronto           0.000000   
50                                               Emery           0.000000   
51                                   

<H4>  Printing each neighborhood with the top 5 most common venues

In [84]:
num_top_venues = 5

for hood in toronto_grouped['Neighbourhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighbourhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide----
              venue  freq
0       Coffee Shop  0.08
1              Café  0.05
2        Steakhouse  0.04
3               Bar  0.03
4  Asian Restaurant  0.03


----Agincourt----
                       venue  freq
0             Breakfast Spot   0.2
1                     Lounge   0.2
2               Skating Rink   0.2
3  Latin American Restaurant   0.2
4             Clothing Store   0.2


----Agincourt North----
                             venue  freq
0                       Playground   0.5
1                             Park   0.5
2                Accessories Store   0.0
3               Mexican Restaurant   0.0
4  Molecular Gastronomy Restaurant   0.0


----Albion Gardens----
                  venue  freq
0         Grocery Store  0.25
1           Pizza Place  0.12
2              Pharmacy  0.12
3  Fast Food Restaurant  0.12
4        Sandwich Place  0.12


----Alderwood----
                venue  freq
0         Pizza Place   0.2
1            Pharmacy   0.1
2         Coffee

<H4> Define a function sorting venues in descending order

In [95]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

<H4> Creating new dataframe and display the top 10 venues for each neighborhood

In [96]:
import numpy as np
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighbourhoods_venues_sorted = pd.DataFrame(columns=columns)
neighbourhoods_venues_sorted['Neighbourhood'] = toronto_grouped['Neighbourhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighbourhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighbourhoods_venues_sorted.head()

Neighbourhood 1st Most Common Venue      2nd Most Common Venue  \
0         Adelaide           Coffee Shop                       Café   
1        Agincourt                Lounge  Latin American Restaurant   
2  Agincourt North                  Park                 Playground   
3   Albion Gardens         Grocery Store       Fast Food Restaurant   
4        Alderwood           Pizza Place               Dance Studio   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0            Steakhouse       Thai Restaurant          Burger Joint   
1          Skating Rink        Breakfast Spot        Clothing Store   
2           Yoga Studio   Dumpling Restaurant                 Diner   
3           Pizza Place        Sandwich Place   Fried Chicken Joint   
4          Skating Rink                   Gym              Pharmacy   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0            Restaurant                   Bar                Bakery   
1     Electronics Store      Doner Restaurant            Donut Shop   
2        Discount Store               Dog Run      Doner Restaurant   
3            Beer Store              Pharmacy   Empanada Restaurant   
4           Coffee Shop                   Pub    Athletics & Sports   

  9th Most Common Venue       10th Most Common Venue  
0      Sushi Restaurant             Asian Restaurant  
1             Drugstore          Dumpling Restaurant  
2            Donut Shop                    Drugstore  
3     Electronics Store  Eastern European Restaurant  
4        Sandwich Place             Doner Restaurant

<H4>Run k-means to cluster the neighborhood into 5 clusters.

In [97]:
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_ 
# to change use .astype()

array([0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 0, 0, 3, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 3,
       0, 0, 0, 0, 0, 3, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0,
       1, 3, 1, 0, 3, 0, 0, 0, 0, 3, 0, 0, 0, 0, 0, 2, 3, 0, 3, 1, 0, 0,
       3, 4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 3, 1, 0, 0, 0, 0, 3, 0, 2,
       0, 0, 0, 0, 3, 0, 0, 3, 0, 0, 0, 1, 0, 0, 0, 0, 4, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 3, 3, 0, 0, 0, 4, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 3, 1,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 3, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 3, 0, 0], dtype=int32)

<H4>Create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [98]:
# add clustering labels
neighbourhoods_venues_sorted.insert(0, 'Cluster_Labels', kmeans.labels_)



In [99]:
toronto_merged = df

In [102]:

toronto_merged = toronto_merged.join(neighbourhoods_venues_sorted.set_index('Neighbourhood'), on='Neighborhood')
toronto_merged.head() 

Postcode           Borough      Neighborhood   Latitude  Longitude  \
0      M3A        North York         Parkwoods  43.753259 -79.329656   
1      M4A        North York  Victoria Village  43.725882 -79.315572   
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636   
3      M6A        North York  Lawrence Heights  43.718518 -79.464763   
4      M6A        North York    Lawrence Manor  43.718518 -79.464763   

   Cluster_Labels   1st Most Common Venue 2nd Most Common Venue  \
0             3.0       Food & Drink Shop                  Park   
1             0.0            Hockey Arena           Pizza Place   
2             0.0             Coffee Shop                  Park   
3             0.0  Furniture / Home Store     Accessories Store   
4             0.0  Furniture / Home Store     Accessories Store   

        3rd Most Common Venue  4th Most Common Venue  \
0  Construction & Landscaping            Yoga Studio   
1                 Coffee Shop  Portuguese Restaurant   
2                         Pub                 Bakery   
3                 Coffee Shop               Boutique   
4                 Coffee Shop               Boutique   

         5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0                      Dog Run      Doner Restaurant            Donut Shop   
1  Eastern European Restaurant        Discount Store               Dog Run   
2                   Restaurant                  Café    Mexican Restaurant   
3           Athletics & Sports   Arts & Crafts Store   Sporting Goods Shop   
4           Athletics & Sports   Arts & Crafts Store   Sporting Goods Shop   

  8th Most Common Venue  9th Most Common Venue       10th Most Common Venue  
0             Drugstore    Dumpling Restaurant  Eastern European Restaurant  
1      Doner Restaurant             Donut Shop                    Drugstore  
2        Cosmetics Shop                    Spa                        Hotel  
3        Clothing Store  Vietnamese Restaurant                Women's Store  
4        Clothing Store  Vietnamese Restaurant                Women's Store

<H4>Droping rows with no data

In [103]:
toronto_merged=toronto_merged.dropna()

In [106]:
toronto_merged['Cluster_Labels'] = toronto_merged.Cluster_Labels.astype(int)

<H4>Display map

In [109]:
# create map
map_clusters = folium.Map(location=[latitude_toronto, longitude_toronto], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster_Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters



<H4> Cluster 1 Analysis

In [110]:
toronto_merged.loc[toronto_merged['Cluster_Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster_Labels   1st Most Common Venue  \
1          North York               0            Hockey Arena   
2    Downtown Toronto               0             Coffee Shop   
3          North York               0  Furniture / Home Store   
4          North York               0  Furniture / Home Store   
5        Queen's Park               0             Coffee Shop   
6    Downtown Toronto               0             Coffee Shop   
7         Scarborough               0    Fast Food Restaurant   
8         Scarborough               0    Fast Food Restaurant   
9          North York               0    Gym / Fitness Center   
10          East York               0    Fast Food Restaurant   
11          East York               0    Fast Food Restaurant   
12   Downtown Toronto               0             Coffee Shop   
13   Downtown Toronto               0             Coffee Shop   
14         North York               0                  Bakery   
20        Scarborough               0           Moving Target   
21        Scarborough               0           Moving Target   
22        Scarborough               0           Moving Target   
23         North York               0                     Gym   
24         North York               0                     Gym   
25          East York               0                    Park   
26   Downtown Toronto               0             Coffee Shop   
27               York               0                   Field   
28          Etobicoke               0            Liquor Store   
29          Etobicoke               0            Liquor Store   
30          Etobicoke               0            Liquor Store   
31          Etobicoke               0            Liquor Store   
32        Scarborough               0     Rental Car Location   
33        Scarborough               0     Rental Car Location   
34        Scarborough               0     Rental Car Location   
35       East Toronto               0                   Trail   
36   Downtown Toronto               0             Coffee Shop   
38        Scarborough               0             Coffee Shop   
39          East York               0             Coffee Shop   
40   Downtown Toronto               0             Coffee Shop   
41   Downtown Toronto               0           Grocery Store   
42        Scarborough               0        Hakka Restaurant   
43         North York               0                 Dog Run   
44         North York               0             Coffee Shop   
45         North York               0             Coffee Shop   
46         North York               0             Coffee Shop   
47          East York               0       Indian Restaurant   
48   Downtown Toronto               0             Coffee Shop   
49   Downtown Toronto               0             Coffee Shop   
50   Downtown Toronto               0             Coffee Shop   
51       West Toronto               0                  Bakery   
52       West Toronto               0                  Bakery   
54         North York               0          Clothing Store   
55         North York               0          Clothing Store   
56         North York               0          Clothing Store   
57         North York               0      Falafel Restaurant   
58         North York               0      Falafel Restaurant   
60   Downtown Toronto               0             Coffee Shop   
61   Downtown Toronto               0             Coffee Shop   
62   Downtown Toronto               0             Coffee Shop   
63       West Toronto               0                     Bar   
64       West Toronto               0                     Bar   
65        Scarborough               0          Discount Store   
66        Scarborough               0          Discount Store   
67        Scarborough               0          Discount Store   
68         North York               0                    Café   
71       East Toronto               0        Gree

<H4>Cluster 2

In [111]:
toronto_merged.loc[toronto_merged['Cluster_Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster_Labels 1st Most Common Venue 2nd Most Common Venue  \
97   North York               1            Food Truck        Baseball Field   
105  North York               1        Baseball Field           Yoga Studio   
106  North York               1        Baseball Field           Yoga Studio   
197   Etobicoke               1        Baseball Field           Yoga Studio   
198   Etobicoke               1        Baseball Field           Yoga Studio   
199   Etobicoke               1        Baseball Field           Yoga Studio   
200   Etobicoke               1        Baseball Field           Yoga Studio   
201   Etobicoke               1        Baseball Field           Yoga Studio   
202   Etobicoke               1        Baseball Field           Yoga Studio   
203   Etobicoke               1        Baseball Field           Yoga Studio   
204   Etobicoke               1        Baseball Field           Yoga Studio   

           3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
97                   Yoga Studio               Dog Run      Doner Restaurant   
105  Eastern European Restaurant               Dog Run      Doner Restaurant   
106  Eastern European Restaurant               Dog Run      Doner Restaurant   
197  Eastern European Restaurant               Dog Run      Doner Restaurant   
198  Eastern European Restaurant               Dog Run      Doner Restaurant   
199  Eastern European Restaurant               Dog Run      Doner Restaurant   
200  Eastern European Restaurant               Dog Run      Doner Restaurant   
201  Eastern European Restaurant               Dog Run      Doner Restaurant   
202  Eastern European Restaurant               Dog Run      Doner Restaurant   
203  Eastern European Restaurant               Dog Run      Doner Restaurant   
204  Eastern European Restaurant               Dog Run      Doner Restaurant   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
97             Donut Shop             Drugstore   Dumpling Restaurant   
105            Donut Shop             Drugstore   Dumpling Restaurant   
106            Donut Shop             Drugstore   Dumpling Restaurant   
197            Donut Shop             Drugstore   Dumpling Restaurant   
198            Donut Shop             Drugstore   Dumpling Restaurant   
199            Donut Shop             Drugstore   Dumpling Restaurant   
200            Donut Shop             Drugstore   Dumpling Restaurant   
201            Donut Shop             Drugstore   Dumpling Restaurant   
202            Donut Shop             Drugstore   Dumpling Restaurant   
203            Donut Shop             Drugstore   Dumpling Restaurant   
204            Donut Shop             Drugstore   Dumpling Restaurant   

           9th Most Common Venue 10th Most Common Venue  
97   Eastern European Restaurant               Festival  
105            Electronics Store                  Field  
106            Electronics Store                  Field  
197            Electronics Store                  Field  
198            Electronics Store                  Field  
199            Electronics Store                  Field  
200            Electronics Store                  Field  
201            Electronics Store                  Field  
202            Electronics Store                  Field  
203            Electronics Store                  Field  
204            Electronics Store                  Field

<H4>Cluster 3

In [112]:
toronto_merged.loc[toronto_merged['Cluster_Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster_Labels 1st Most Common Venue 2nd Most Common Venue  \
15  Etobicoke               2          Home Service           Yoga Studio   
16  Etobicoke               2          Home Service           Yoga Studio   
17  Etobicoke               2          Home Service           Yoga Studio   
18  Etobicoke               2          Home Service           Yoga Studio   
19  Etobicoke               2          Home Service           Yoga Studio   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
15               Dog Run      Doner Restaurant            Donut Shop   
16               Dog Run      Doner Restaurant            Donut Shop   
17               Dog Run      Doner Restaurant            Donut Shop   
18               Dog Run      Doner Restaurant            Donut Shop   
19               Dog Run      Doner Restaurant            Donut Shop   

   6th Most Common Venue 7th Most Common Venue        8th Most Common Venue  \
15             Drugstore   Dumpling Restaurant  Eastern European Restaurant   
16             Drugstore   Dumpling Restaurant  Eastern European Restaurant   
17             Drugstore   Dumpling Restaurant  Eastern European Restaurant   
18             Drugstore   Dumpling Restaurant  Eastern European Restaurant   
19             Drugstore   Dumpling Restaurant  Eastern European Restaurant   

   9th Most Common Venue 10th Most Common Venue  
15     Electronics Store                  Diner  
16     Electronics Store                  Diner  
17     Electronics Store                  Diner  
18     Electronics Store                  Diner  
19     Electronics Store                  Diner

<H4> Cluster 4

In [113]:
toronto_merged.loc[toronto_merged['Cluster_Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster_Labels 1st Most Common Venue  \
0          North York               3     Food & Drink Shop   
37               York               3                  Park   
59          East York               3                  Park   
69         North York               3                  Park   
70         North York               3                  Park   
111   Central Toronto               3                  Park   
115              York               3                  Park   
119        North York               3                  Park   
136         Etobicoke               3                  Park   
137         Etobicoke               3                  Park   
138         Etobicoke               3                  Park   
139         Etobicoke               3                  Park   
154       Scarborough               3                  Park   
155       Scarborough               3                  Park   
156       Scarborough               3                  Park   
157       Scarborough               3                  Park   
182  Downtown Toronto               3                  Park   
192         Etobicoke               3                  Park   
193         Etobicoke               3                  Park   
194         Etobicoke               3                  Park   

    2nd Most Common Venue        3rd Most Common Venue  \
0                    Park   Construction & Landscaping   
37   Fast Food Restaurant                Women's Store   
59            Coffee Shop            Convenience Store   
69                Airport                  Yoga Studio   
70                Airport                  Yoga Studio   
111           Swim School                     Bus Line   
115           Yoga Studio  Eastern European Restaurant   
119                  Bank            Convenience Store   
136           Pizza Place            Mobile Phone Shop   
137           Pizza Place            Mobile Phone Shop   
138           Pizza Place            Mobile Phone Shop   
139           Pizza Place            Mobile Phone Shop   
154            Playground                  Yoga Studio   
155            Playground                  Yoga Studio   
156            Playground                  Yoga Studio   
157            Playground                  Yoga Studio   
182                 Trail                   Playground   
192                  Pool                        River   
193                  Pool                        River   
194                  Pool                        River   

           4th Most Common Venue        5th Most Common Venue  \
0                    Yoga Studio                      Dog Run   
37                        Market          Dumpling Restaurant   
59                   Yoga Studio  Eastern European Restaurant   
69   Eastern European Restaurant               Discount Store   
70   Eastern European Restaurant               Discount Store   
111                    Drugstore               Discount Store   
115               Discount Store                      Dog Run   
119                  Yoga Studio  Eastern European Restaurant   
136          Dumpling Restaurant               Discount Store   
137          Dumpling Restaurant               Discount Store   
138          Dumpling Restaurant               Discount Store   
139          Dumpling Restaurant               Discount Store   
154          Dumpling Restaurant                        Diner   
155          Dumpling Restaurant                        Diner   
156          Dumpling Restaurant                        Diner   
157          Dumpling Restaurant                        Diner   
182                        Diner               Discount Store   
192      Comfort Food Restaurant                 Dessert Shop   
193      Comfort Food Restaurant                 Dessert Shop   
194      Comfort Food Restaurant                 Dessert Shop   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0        Doner Restaurant       

<H4>Cluster 5

In [114]:
toronto_merged.loc[toronto_merged['Cluster_Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster_Labels 1st Most Common Venue  \
53       Scarborough               4            Playground   
149  Central Toronto               4            Restaurant   
150  Central Toronto               4            Restaurant   

    2nd Most Common Venue        3rd Most Common Venue 4th Most Common Venue  \
53            Yoga Studio  Eastern European Restaurant        Discount Store   
149            Playground                  Yoga Studio             Drugstore   
150            Playground                  Yoga Studio             Drugstore   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
53                Dog Run      Doner Restaurant            Donut Shop   
149                 Diner        Discount Store               Dog Run   
150                 Diner        Discount Store               Dog Run   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
53              Drugstore   Dumpling Restaurant      Electronics Store  
149      Doner Restaurant            Donut Shop    Dumpling Restaurant  
150      Doner Restaurant            Donut Shop    Dumpling Restaurant